In [1]:
import pickle

import altair as alt

import pandas as pd

import polyclonal

import warnings
warnings.filterwarnings('ignore')

from IPython.utils import io

In [2]:
import altair_saver

In [3]:
import os
os.chdir('../../../')

## Plotting immune escape across full protein and selected sites

In [4]:
def get_summed_escapes(sera_list, cohort):
    summed_escape_list = []
    
    for serum in sera_list:
        prob_escape = pd.read_csv(
            f'results/antibody_escape/{serum}_avg.csv'
        ).query(
            "`times_seen` >= 5"
        )
        
        prob_escape_sum = (
            prob_escape.groupby(['site', 'wildtype'], as_index=False)
            .aggregate({'escape_mean': 'sum'})
            .rename(columns={'escape_mean': 'escape'})
        ) 
            
        prob_escape_sum['serum'] = serum
        prob_escape_sum['cohort'] = cohort
        
        summed_escape_list.append(prob_escape_sum)
        
    summed_escape = pd.concat(summed_escape_list)
    return summed_escape

Get HK19 data:

In [5]:
# define samples in each age cohort
peds = [3944, 2389, 2323, 2388, 3973, 4299, 4584, 2367]
teens = [2350, 2365, 2382, 3866, 2380, 3856, 3857, 3862]
adults = ['33C', '34C', '197C', '199C', '215C', 
          '210C', '74C', '68C', '150C', '18C',]
elderly = ['AUSAB-13']
infant = [2462]

sample_lists = [peds, teens, adults, elderly, infant]
cohorts = ['2-5 years', '15-20 years', '40-45 years',  '68 years', 'infant']
cohort_dfs = []

i=0 # for looping through age cohort definitions

# start by getting full escape df for HK19
for entry in sample_lists:
    cohort_escape_df = get_summed_escapes(entry, cohorts[i])
    cohort_dfs.append(cohort_escape_df)

    i+=1

hk19_df = pd.concat(cohort_dfs)

hk19_df['serum'] = hk19_df['serum'].astype(str)

# add 'escape_mean' column of mean escape values per site within an age group
hk19_df['escape_mean'] = (
    hk19_df.groupby(['site', 'cohort'])['escape']
    .transform('mean')
)

hk19_df['ha_strain'] = 'hk19'

Get Perth09 data:

In [6]:
# define samples in each age cohort
sample_dict = {
    "2-4 years": [
        "age 2.1 (Vietnam)", 
        "age 2.2 (Vietnam)",
        "age 2.4 (Vietnam)",
        "age 2.5 (Vietnam)",
        "age 2.5b (Vietnam)",
        "age 3.3 (Vietnam)", 
        "age 3.3b (Vietnam)",
        "age 3.4 (Vietnam)", 
        "age 3.5 (Vietnam)",
    ],   
    "30-34 years": [
        "age 30.5 (Vietnam)",
        "age 31.5 (Vietnam)",
        "age 33.5 (Vietnam)",
    ],
    "misc_adult": [
        "age 21 (Seattle)",
        "age 53 (Seattle)",
        "age 64 (Seattle)",
        "age 65 (Seattle)",
    ],
    "ferret": [
        "ferret 1 (Pitt)",
        "ferret 2 (Pitt)",
        "ferret 3 (Pitt)",
        "ferret (WHO)",
    ]
}

# get full dataset
perth09_df = pd.read_csv(f'results/perth2009/merged_escape.csv')[['name', 'site', 'wildtype', 'mutant', 'escape']]
perth09_df = perth09_df.rename(columns={'name': 'serum'})

# Function to convert '(HA2)X' to numeric
def convert_site_to_numeric(site):
    if '(HA2)' in site:
        try:
            number = int(site.replace('(HA2)', '').strip())
            return number + 329
        except ValueError:
            return site  # If there's an issue with conversion, return the original value
    else:
        return site

# Apply the function to the 'site' column
perth09_df['site'] = perth09_df['site'].apply(convert_site_to_numeric)

# get summed escape at each site
perth09_df = perth09_df.groupby(['serum', 'site', 'wildtype'], as_index=False).aggregate({'escape': 'sum'})

# floor at 0
perth09_df['escape'] = perth09_df['escape'].clip(lower=0)

# add cohort label
def find_sample_type(sample_name):
    for sample_type, sample_list in sample_dict.items():
        if sample_name in sample_list:
            return sample_type
    return None

perth09_df['cohort'] = perth09_df['serum'].apply(find_sample_type)

perth09_df = perth09_df.loc[(perth09_df['cohort'] != 'misc_adult')]
perth09_df['site'] = perth09_df['site'].astype(int)

# add 'escape_mean' column of mean escape values per site within a cohort
perth09_df['escape_mean'] = (
    perth09_df.groupby(['site', 'cohort'])['escape']
    .transform('mean')
)

perth09_df['ha_strain'] = 'perth09'

Combine to a single dataframe, and label antigenic regions:

In [7]:
# make single full dataframe
escape_df = pd.concat([perth09_df, hk19_df])

# add antigenic region labels
site_A = list(range(121, 147))
site_B = list(range(155, 161)) + list(range(186, 199))
site_C = list(range(44, 55)) + list(range(273, 281))
site_D = list(range(201,220))
site_E = list(range(62, 66)) + list(range(78, 95)) + list(range(260, 266))

antigenic_regions = {
    'A': site_A, 
    'B': site_B, 
    'C': site_C, 
    'D': site_D,
    'E': site_E
}

# Function to map sites to antigenic regions
def map_site_to_antigenic_region(site):
    for region, sites in antigenic_regions.items():
        if site in sites:
            return region
    return None  # Handle the case where the site doesn't belong to any region

# Apply the mapping function to create the 'antigenic region' column
escape_df['antigenic_region'] = escape_df['site'].map(map_site_to_antigenic_region)

### Filter to selected sites and normalize

In [14]:
# define list of key sites
# site_list = [48, 50, 156, 157, 159, 160, 186, 188, 189, 192, 193, 275, 276]

site_list = [48, 50, 81, 82, 121, 122, 124, 131, 135, 137, 145, 156, 157, 
              159, 160, 186, 188, 189, 192, 193, 275, 276]

# filter dataframe
escape_df_filtered = escape_df[escape_df['site'].isin(site_list)]

escape_df_filtered['site'] = escape_df_filtered['site'].astype(str)

Generate normalized version of the dataframe:

In [15]:
# Group the DataFrame by the 'serum' column
grouped = escape_df_filtered.groupby('serum')

# Define a function to normalize the 'escape_mean' column within each group
def normalize(group):
    group['escape'] = group['escape'] / group['escape'].max()
    return group

# Apply the normalization function to each group
normalized_df = grouped.apply(normalize)

# Reset the index of the resulting DataFrame
normalized_df.reset_index(drop=True, inplace=True)

# set lower bound to 0
normalized_df['escape'] = normalized_df['escape'].clip(lower=0)

# replace mean_escape_mean values
normalized_df['escape_mean'] = (
    normalized_df.groupby(['site', 'cohort'])['escape']
    .transform('mean')
)

## Set up different chart options

In [16]:
site_order = ['121', '122', '124', '131', '135', '137', '142', '144', '145', 
              '156', '157', '159', '160', '186', '188', '189', '192', '193', 
              '48', '50', '275', '276', 
              '81', '82']  

In [17]:
def filtered_site_plot(filtered_df, ha_strain, y_domain, axis_values=None):
    
    filtered_df = filtered_df.loc[filtered_df['ha_strain'] == ha_strain]
    
    if ha_strain == 'hk19':
        cohort_order = ['2-5 years', '15-20 years', '40-45 years', '68 years', 'infant']
    
    if ha_strain == 'perth09':
        cohort_order = ['2-4 years', '30-34 years', 'ferret']

    if axis_values:
        filtered_sites_lineplot = (
            alt.Chart()
            .encode(
                x=alt.X("site", 
                        title="site",
                        sort=site_order                 
                       ),
                y=alt.Y(
                    "escape",
                    scale=alt.Scale(domain=y_domain),
                    title="escape score",
                    axis=alt.Axis(values=axis_values),
                ),
                color=alt.Color('cohort:N', 
                                legend=None
                               ).scale(scheme='dark2',
                                       domain=cohort_order
                                      ),
                # detail='serum',
                detail=alt.Detail(['serum', 'antigenic_region']),
                tooltip=['serum', 'site', 'escape']
            )
            .mark_line(size=2.7, opacity=0.3, clip=True)
            .properties(width=500, height=130)
        )
        
    else:
        filtered_sites_lineplot = (
            alt.Chart()
            .encode(
                x=alt.X("site", 
                        title="site",
                        sort=site_order                 
                       ),
                y=alt.Y(
                    "escape",
                    scale=alt.Scale(domain=y_domain),
                    title="escape score",
                ),
                color=alt.Color('cohort:N', 
                                legend=None
                               ).scale(scheme='dark2',
                                       domain=cohort_order
                                      ),
                # detail='serum',
                detail=alt.Detail(['serum', 'antigenic_region']),
                tooltip=['serum', 'site', 'escape']
            )
            .mark_line(size=2.7, opacity=0.3, clip=True)
            .properties(width=500, height=130)     
        )
    
    mean_points = (
        alt.Chart()
        .encode(
            x=alt.X("site", 
                    title="site",
                    sort=site_order,
                   ),
            y=alt.Y("escape_mean"),
            color=alt.Color('cohort:N', legend=None).scale(scheme='dark2'),
            tooltip=['site', 'escape_mean']
        )
        .mark_circle(size=55, opacity=0.75)
    )
    
    x_axis = alt.Chart(pd.DataFrame({'y': [0]})).mark_rule(
        size=1, 
        opacity=0.5, color='gray').encode(y='y')
    
    faceted_overlay = alt.layer(
        filtered_sites_lineplot, x_axis, data=filtered_df
    ).facet(
        facet=alt.Facet(
            'cohort:N',
            sort=cohort_order,
            title='summed escape',
            header=alt.Header(
                titleFontSize=21,
                titleFontWeight='normal',
                titlePadding=5,
                labelFontSize=17,
                labelOrient='right',
                # labelAngle=0,
                labelFontStyle='italic'
            )
        ),
        spacing=3,
        columns=1
    ).configure_axis(
        grid=False,
        labelFontSize=14,
        titleFontSize=15
    )   

    return faceted_overlay

In [18]:
def full_escape_plot(df, ha_strain, x_domain=[0, 540], y_domain=[-12.5, 12.5]):
    
    df = df.loc[df['ha_strain'] == ha_strain]

    escape_lineplot = (
        alt.Chart()
        .encode(
            x=alt.X("site", 
                    title="site",
                    scale=alt.Scale(domain=x_domain,
                                    clamp=True
                                   )
                   ),
            y=alt.Y(
                "escape",
                title=None,
                scale=alt.Scale(domain=y_domain,
                                clamp=True
                               )
            ),
            color=alt.Color('cohort:N', 
                            legend=None,
                           ).scale(scheme='dark2'),
            detail='serum',
            tooltip=['serum', 'site', 'escape']
        )
        .mark_line(size=.75, opacity=0.7)
        .properties(width=600, height=70)
    )
    
    faceted_lineplot = alt.layer(
        escape_lineplot, data=df
    ).facet(
        facet=alt.Facet(
            'cohort:N',
            title='escape at all residues',
            header=alt.Header(
                titleFontSize=21,
                titleFontWeight='normal',
                titlePadding=5,
                labelFontSize=1,
                labelOrient='right',
            )
        ),
        spacing=2,
        columns=1
    ).configure_axis(
        grid=False,
        labelFontSize=13,
        titleFontSize=15
    )
    
    return faceted_lineplot

In [59]:
perth09_site_plot = filtered_site_plot(escape_df_filtered, 'perth09', y_domain=[-1, 45])

# perth09_site_plot.save(
#     'scratch_notebooks/figure_drafts/sitewise_escape/perth09_filt_escape.png',
#     scale_factor=2.0
# )

perth09_site_plot

alt.FacetChart(...)

In [60]:
hk19_site_plot = filtered_site_plot(escape_df_filtered, 'hk19', y_domain=[-12.5, 12.5])

# hk19_site_plot.save(
#     'scratch_notebooks/figure_drafts/sitewise_escape/hk19_filt_escape.png',
#     scale_factor=2.0
# )

hk19_site_plot

alt.FacetChart(...)

In [61]:
perth09_normalized = filtered_site_plot(normalized_df, 'perth09', y_domain=[-0.1, 1.1], axis_values=[0, 0.5, 1])

# perth09_normalized.save(
#     'scratch_notebooks/figure_drafts/sitewise_escape/perth09_filt_escape_normalized.png',
#     scale_factor=2.0
# )

perth09_normalized

alt.FacetChart(...)

In [62]:
hk19_normalized = filtered_site_plot(normalized_df, 'hk19', y_domain=[-0.1, 1.1], axis_values=[0, 0.5, 1])

# hk19_normalized.save(
#     'scratch_notebooks/figure_drafts/sitewise_escape/hk19_filt_escape_normalized.png',
#     scale_factor=2.0
# )

hk19_normalized

alt.FacetChart(...)

In [63]:
full_escape_plot(escape_df, 'hk19')

alt.FacetChart(...)

In [64]:
full_escape_plot(escape_df, 'perth09', y_domain=[-5, 55])

alt.FacetChart(...)

In [21]:
pediatric_df = escape_df_filtered.loc[escape_df_filtered['cohort'].isin(['2-4 years', '2-5 years'])]

# define dark2 colors
dark2_colors = ['#1b9e77', '#d95f02', '#7570b3', '#e7298a', '#66a61e', '#e6ab02', '#a6761d', '#666666']

ped_color_scheme = alt.Scale(
    domain=['2-5 years', '2-4 years'],  # Your cohort values
    range=[dark2_colors[2], dark2_colors[1]]  # Use the 2nd and 3rd colors from 'dark2'
)

filtered_sites_lineplot = (
    alt.Chart()
    .encode(
        x=alt.X("site", 
                title="site",
                sort=site_order                 
               ),
        y=alt.Y(
            "escape",
            scale=alt.Scale(domain=[-12.5, 12.5]),
            title="escape score",
        ),
        color=alt.Color('cohort:N', 
                        legend=None
                       ).scale(ped_color_scheme),  # Use the custom color scheme
        detail=alt.Detail(['serum', 'antigenic_region']),
        tooltip=['serum', 'site', 'escape']
    )
    .mark_line(size=2, opacity=0.25, clip=True)
    .properties(width=275, height=130)
)

mean_points = (
    alt.Chart()
    .encode(
        x=alt.X("site", 
                title="site",
                sort=site_order,
               ),
        y=alt.Y("escape_mean"),
        color=alt.Color('cohort:N', legend=None).scale(ped_color_scheme),  # Use the custom color scheme
        tooltip=['site', 'escape_mean']
    )
    .mark_circle(size=55, opacity=0.75)
)

x_axis = alt.Chart(pd.DataFrame({'y': [0]})).mark_rule(
    size=1, 
    opacity=0.5, color='gray').encode(y='y')

faceted_overlay = alt.layer(
    filtered_sites_lineplot, mean_points, x_axis, data=pediatric_df
).facet(
    facet=alt.Facet(
        'cohort:N',
        title='summed escape',
        header=alt.Header(
            titleFontSize=21,
            titleFontWeight='normal',
            titlePadding=5,
            labelFontSize=17,
            labelOrient='right',
            # labelAngle=0,
            labelFontStyle='italic'
        )
    ),
    spacing=3,
    columns=1
).configure_axis(
    grid=False,
    labelFontSize=14,
    titleFontSize=15
)   

faceted_overlay.save(
    'scratch_notebooks/figure_drafts/sitewise_escape/ped-plot_hk19.png',
    scale_factor=2.0
)

faceted_overlay

alt.FacetChart(...)

In [14]:
selected_cohorts = ['2-4 years', '30-34 years', '2-5 years', '15-20 years', '40-45 years']

normalized_df_filtered = normalized_df[normalized_df['cohort'].isin(selected_cohorts)]

normalized_df_filtered

serum site wildtype    escape       cohort  escape_mean  \
0                  150C   48        I  0.009868  40-45 years     0.100624   
1                  150C   50        E  0.000000  40-45 years     0.036917   
2                  150C   81        N  0.000000  40-45 years     0.011578   
3                  150C   82        K  0.057683  40-45 years     0.045015   
4                  150C  121        K  0.000000  40-45 years     0.000000   
..                  ...  ...      ...       ...          ...          ...   
875  age 33.5 (Vietnam)  276        K  0.000000  30-34 years     0.000000   
876  age 33.5 (Vietnam)   48        T  0.000000  30-34 years     0.000000   
877  age 33.5 (Vietnam)   50        E  0.000000  30-34 years     0.000000   
878  age 33.5 (Vietnam)   81        N  0.000000  30-34 years     0.000000   
879  age 33.5 (Vietnam)   82        K  0.000000  30-34 years     0.000000   

    ha_strain antigenic_region  
0        hk19                C  
1        hk19                C  
2        hk19                E  
3        hk19                E  
4        hk19                A  
..        ...              ...  
875   perth09                C  
876   perth09                C  
877   perth09                C  
878   perth09                E  
879   perth09                E  

[836 rows x 8 columns]

In [19]:
filtered_sites_lineplot = (
    alt.Chart()
    .encode(
        x=alt.X("site", 
                title="site",
                sort=site_order                 
               ),
        y=alt.Y(
            "escape",
            scale=alt.Scale(domain=[-0.1, 1.1]),
            title="escape score",
            axis=alt.Axis(values=[0, 0.5, 1]),
        ),
        color=alt.Color('cohort:N', 
                        # sort=['2-5 years', '15-20 years', '40-45 years', '2-4 years', '30-34 years']
                        # legend=None
                       ).scale(scheme='dark2'),
        detail=alt.Detail(['serum', 'antigenic_region']),
        tooltip=['serum', 'site', 'escape']
    )
    .mark_line(size=2, opacity=0.2, clip=True)
    .properties(width=500, height=130)
)

faceted_lineplot = alt.layer(
    filtered_sites_lineplot, data=normalized_df_filtered
).facet(
    facet=alt.Facet(
        'ha_strain:N',
        sort=['perth09', 'hk19'],
        title='normalized positive escape',
        header=alt.Header(
            titleFontSize=21,
            titleFontWeight='normal',
            titlePadding=5,
            labelFontSize=17,
            labelOrient='right',
            # labelAngle=0,
            labelFontStyle='italic'
        )
    ),
    spacing=3,
    columns=1
    ).configure_axis(
    grid=False,
    labelFontSize=14,
    titleFontSize=15
    )   


faceted_lineplot.save(
    'scratch_notebooks/figure_drafts/sitewise_escape/library_overlay.png',
    scale_factor=2.0
)

faceted_lineplot

alt.FacetChart(...)

In [68]:
hk19_df = escape_df_filtered[(escape_df_filtered['ha_strain'] == 'hk19') & 
                             (escape_df_filtered['cohort'] != 'infant') 
                            ]

hk19_layered = (
    alt.Chart(hk19_df)
    .encode(
        x=alt.X("site", 
                title="site",
                sort=site_order                 
               ),
        y=alt.Y(
            "escape",
            scale=alt.Scale(domain=[-12.5, 12.5]),
            title="escape score",
        ),
        color=alt.Color('cohort:N', 
                        sort=['2-5 years', '15-20 years', '40-45 years', '68 years'],
                        legend=None
                       ).scale(scheme='dark2'),
        detail=alt.Detail(['serum', 'antigenic_region']),
        tooltip=['serum', 'site', 'escape']
    )
    .mark_line(size=2, opacity=0.3, clip=True)
    .properties(width=500, height=130)
    .configure_axis(
        grid=False,
        labelFontSize=14,
        titleFontSize=15
    )
)

hk19_layered.save(
    'scratch_notebooks/figure_drafts/sitewise_escape/hk19_overlay.png',
    scale_factor=2.0
)

hk19_layered

alt.Chart(...)

In [70]:
df_filtered_ped = escape_df_filtered[escape_df_filtered['cohort'] == '2-5 years']

In [73]:
hk19_ped = filtered_site_plot(df_filtered_ped, 'hk19', y_domain=[-12.5, 12.5])

hk19_ped.save(
    'scratch_notebooks/figure_drafts/sitewise_escape/hk19_ped.png',
    scale_factor=2.0
)

hk19_ped

alt.FacetChart(...)

In [12]:
# filtered sites, line and scatter overlay
summed_escape_lineplot = (
    alt.Chart()
    .encode(
        x=alt.X("site", 
                title="site",
                sort=site_order                 
               ),
        y=alt.Y(
            "escape_mean",
            scale=alt.Scale(domain=[-12.5, 12.5]),
            title="escape score",
        ),
        color=alt.Color('age_group:N', 
                        legend=None
                       ).scale(scheme='dark2'),
        detail='serum',
        tooltip=['serum', 'site', 'escape_mean']
    )
    .mark_line(size=1, opacity=0.4, clip=True)
    .properties(width=500, height=130)
)

mean_points = (
    alt.Chart()
    .encode(
        x=alt.X("site", 
                title="site",
                sort=site_order   
               ),
        y=alt.Y("mean_escape_mean"),
        color=alt.Color('age_group:N', legend=None).scale(scheme='set2'),
        tooltip=['site', 'escape_mean']
    )
    .mark_circle(size=30, opacity=0.75)
    # .properties(width=400, height=150)
)

x_axis = alt.Chart(pd.DataFrame({'y': [0]})).mark_rule(
    size=1, 
    opacity=0.5, color='gray').encode(y='y')

faceted_line_scatter_overlay = alt.layer(
    summed_escape_lineplot, data=escape_df_filtered
# ).facet(
#     facet=alt.Facet(
#         'age_group:N',
#         title='summed escape',
#         header=alt.Header(
#             titleFontSize=21,
#             titleFontWeight='normal',
#             titlePadding=5,
#             labelFontSize=17,
#             labelOrient='right',
#             # labelAngle=0,
#             labelFontStyle='italic'
#         )
#     ),
#     spacing=3,
#     columns=1
).configure_axis(
    grid=False,
    labelFontSize=14,
    titleFontSize=15
)

faceted_line_scatter_overlay.save(
    'scratch_notebooks/figure_drafts/sitewise_escape/23090912_filt_escape_overlay.png',
    scale_factor=2.0
)

faceted_line_scatter_overlay

alt.LayerChart(...)

In [18]:
site_brush = alt.selection_interval(
    encodings=["x"],
    mark=alt.BrushConfig(stroke="black", strokeWidth=2),
)

site_zoom_bar = (
    alt.Chart(escape_df_full)
    .mark_rect()
    .encode(
        x=alt.X(
            "site:O",
            sort=alt.EncodingSortField(field="_stat_site_order", order="ascending"),
        ),
        color=(
            alt.Color(
                'antigenic_region:N',
                # scale=alt.Scale(scheme=site_zoom_bar_color_scheme),
                legend=alt.Legend(orient="left"),
                # sort=(
                #     site_zoom_bar_df.set_index("site")
                #     .loc[sites]['antigenic_region']
                #     .unique()
                # ),
            )
            # if site_zoom_bar_color_col
            # else alt.value("gray")
        ),
        # tooltip=[c for c in site_zoom_bar_df.columns if not c.startswith("_stat")],
    )
    .mark_rect()
    # .add_params(site_brush)
    .properties(width=500, height=10, title="site zoom bar")
)

site_zoom_bar

alt.Chart(...)

In [ ]:
# create site zoom bar
    site_brush = alt.selection_interval(
        encodings=["x"],
        mark=alt.BrushConfig(stroke="black", strokeWidth=2),
    )
    if site_zoom_bar_color_col:
        assert site_zoom_bar_color_col not in {"_n", "_drop"}, site_zoom_bar_color_col
        site_zoom_bar_df = (
            data_df[["site", "_stat_site_order", site_zoom_bar_color_col]]
            .drop_duplicates()
            .assign(
                _n=lambda x: (
                    x.groupby("site")[site_zoom_bar_color_col].transform("size")
                ),
                _drop=lambda x: (
                    x[site_zoom_bar_color_col]
                    .isnull()
                    .where(
                        x["_n"] > 1,
                        False,
                    )
                ),
            )
            .query("not _drop")
            .drop(columns=["_n", "_drop"])
        )
        site_zoom_bar_df[site_zoom_bar_color_col] = site_zoom_bar_df[
            site_zoom_bar_color_col
        ].fillna("null")
        if any(site_zoom_bar_df.groupby("site").size() > 1):
            raise ValueError(
                f"multiple {site_zoom_bar_color_col=} values for sites:"
                + str(
                    site_zoom_bar_df.assign(
                        n=lambda x: (
                            x.groupby("site")[site_zoom_bar_color_col].transform("size")
                        ),
                    )
                    .sort_values("n", ascending=False)
                    .reset_index(drop=True)
                )
            )
    else:
        site_zoom_bar_df = data_df[["site", "_stat_site_order"]].drop_duplicates()
    site_zoom_bar = (
        alt.Chart(site_zoom_bar_df)
        .mark_rect()
        .encode(
            x=alt.X(
                "site:O",
                sort=alt.EncodingSortField(field="_stat_site_order", order="ascending"),
            ),
            color=(
                alt.Color(
                    site_zoom_bar_color_col,
                    type="nominal",
                    scale=alt.Scale(scheme=site_zoom_bar_color_scheme),
                    legend=alt.Legend(orient="left"),
                    sort=(
                        site_zoom_bar_df.set_index("site")
                        .loc[sites][site_zoom_bar_color_col]
                        .unique()
                    ),
                )
                if site_zoom_bar_color_col
                else alt.value("gray")
            ),
            tooltip=[c for c in site_zoom_bar_df.columns if not c.startswith("_stat")],
        )
        .mark_rect()
        .add_params(site_brush)
        .properties(width=site_zoom_bar_width, height=cell_size, title="site zoom bar")
    )

